### Import Libraries

In [10]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
import torch.distributions as dist
from torchsummary import summary
import math
import os
import numpy as np
import time
import matplotlib.pyplot as plt
from prettytable import PrettyTable
from sklearn.model_selection import train_test_split
from tqdm import tqdm
from pathlib import Path
import re
from skimage.metrics  import structural_similarity as ssim

from importlib import reload
import visualization

# locals
import model_architectures

reload(model_architectures)
from model_architectures import VAE, Data3D, ResnetEncoder, ResnetEncoderHalf

reload(visualization)
from visualization import brain_diff

### Define Paths

In [2]:
research_dir = r"D:/school/research"
code_dir = os.path.join(research_dir, "code")
model_dir = os.path.join(code_dir, "explore_again", "models")
data_dir = os.path.join(research_dir, "data")
dhcp_rel2 = os.path.join(data_dir, "dhcp_rel2")
processed_dir = os.path.join(dhcp_rel2, "processed")
volume_dir = os.path.join(processed_dir, "volumes")
l1_dir = os.path.join(volume_dir, "l1")
l5_dir = os.path.join(volume_dir, "l5")

### Get Data

In [3]:
np.random.seed(42)
num_samples = int(len(os.listdir(l1_dir)) / 2)
samples = np.array([i for i in range(0, num_samples)])
np.random.shuffle(samples)

split_val = int(0.8 * num_samples)
train_indices = samples[0:split_val]
val_indices = samples[split_val:]

num_test = int(len(os.listdir(l5_dir)) / 2)
test_indices = np.array([i for i in range(0, num_test)])

In [4]:
train = Data3D(l1_dir, train_indices, t2_only=False)
val = Data3D(l1_dir, val_indices, t2_only=False)
test = Data3D(l5_dir, test_indices, t2_only=False)

batch_size = 1
train_loader = DataLoader(train, batch_size=batch_size)#, num_workers=1)
val_loader = DataLoader(val, batch_size=batch_size)#, num_workers=1)

### Get State Dict

In [5]:
model_path = os.path.join(model_dir, "vae_rel2_t1_t2_second_session.pt")
state_dict = torch.load(model_path)

In [6]:
state_dict.keys()

odict_keys(['model.0.pass1.2.weight', 'model.0.pass1.2.bias', 'model.0.pass2.2.weight', 'model.0.pass2.2.bias', 'model.0.conv_bypass.weight', 'model.0.conv_bypass.bias', 'model.1.pass1.2.weight', 'model.1.pass1.2.bias', 'model.1.pass2.2.weight', 'model.1.pass2.2.bias', 'model.1.conv_bypass.weight', 'model.1.conv_bypass.bias', 'model.2.pass1.2.weight', 'model.2.pass1.2.bias', 'model.2.conv_bypass.weight', 'model.2.conv_bypass.bias', 'model.3.mu.weight', 'model.3.mu.bias', 'model.3.sigma.weight', 'model.3.sigma.bias', 'model.3.dense_out.weight', 'model.3.dense_out.bias', 'model.4.pass1.2.up.0.weight', 'model.4.pass1.2.up.0.bias', 'model.4.conv_bypass.weight', 'model.4.conv_bypass.bias', 'model.5.pass1.2.up.0.weight', 'model.5.pass1.2.up.0.bias', 'model.5.pass2.2.up.0.weight', 'model.5.pass2.2.up.0.bias', 'model.5.conv_bypass.weight', 'model.5.conv_bypass.bias', 'model.6.pass1.2.up.0.weight', 'model.6.pass1.2.up.0.bias', 'model.6.pass2.2.up.0.weight', 'model.6.pass2.2.up.0.bias', 'model.6

In [34]:
class VAEEncoder(nn.Module):
    def __init__(self, channels):
        super().__init__()
        
        self.model = nn.Sequential(
            ResnetEncoder(channels),
            # ResnetEncoder(32),
            # ResnetEncoderHalf(32)
        )
        
    def forward(self, x):
        x = self.model(x)
        
        return x

In [35]:
model = VAEEncoder(2)
model_dict = model.state_dict()
pretrained_dict = {k: v for k,v in state_dict.items() if k in model_dict}
model_dict.update(pretrained_dict)
model.load_state_dict(pretrained_dict)

<All keys matched successfully>

In [38]:
x = torch.Tensor(np.reshape(train[0], (1, 2, 256, 256, 256)))
x_hat = model(x)
pred = np.reshape(x_hat.detach().numpy(), (32, 64, 64, 64))

In [52]:
ax[63]

<AxesSubplot:>

In [56]:
channel = 2
fig, ax = plt.subplots(64, 32, figsize=(100, 100))

for i in range(0, 32):
    for j in range(0, 64):
        ax[j][i].imshow(pred[i][:,:,j])
        ax[j][i].axis('off')